In [ ]:
import numpy as np
import urllib.parse
import time
import os
import shutil
import re
import copy

from bokeh.plotting import figure, output_file, save
from bokeh.layouts import column, row, gridplot
from bokeh.models import Div, ColumnDataSource, LabelSet
from bokeh.models.annotations import Title
from bokeh.models.widgets import Panel, Tabs

from vis.robot_dynamics.motion_comfort import MotionComfort


def read_test_list(input_path):
    # Read in .tsv at input_path and return dictionary of the data.
    # Format of output:
    #   tests = { 'length': number of tests,
    #             'ids': list of ids,
    #             'dropped': list of ids for ignored data,
    #             'total_improvement': None
    #             'total_fractions': [[0,0,0],[0,0,0]]
    #             id_number(int): {
    #                              'name': name of test,
    #                              'title': title of test,
    #                              'result': [Control result, Comparison result],
    #                              'uri': [Control URI, Comparison URI],
    #                              'length': [None,None]
    #                              'improve': None,
    #                              'change': None,
    #                              'fractions': [None,None],
    #                              'dropped': list of ids for ignored data,
    #                              'unix_time': [None, None],
    #                              'distance': [None, None]
    #                             }
    #           }
    
    file = open(input_path,'r')
    lines = file.readlines()
    
    lines_to_skip = 1
    
    n_test = len(lines)-lines_to_skip
    
    tests = {'ids':[],'dropped':[],'total_improve':None, 'total_fractions': [[0,0,0],[0,0,0]]}
    
    for i in range(n_test):
        line = lines[i+lines_to_skip].strip().split('\t')
        if len(line) == 6:
            tests['ids'].append(i+1)
            tests[i+1] = {'name':line[0],
                          'title':line[1],
                          'result':[line[2], line[4]],
                          'uri':[line[3], line[5]],
                          'length': [None, None],
                          'improve': None,
                          'change': None,
                          'fractions': [None, None],
                          'comfort': [None, None],
                          'unix_time': [None, None],
                          'distance': [None, None]}
        else:
             tests['dropped'].append(i+1)

    tests['length'] = len(tests['ids'])
    return tests


def compare_fractions(f1_cf, f2_cf):
    # Compare 2 motion_comfort() fractions lists, f1_cf and f2_cf
    # returns improve, change
    #     where change = f2_cf - f1_cf (element-wise subtraction)
    #     and improve is an integer -1 = got worse, 0 = no change, 1 = got better
    #     Note: only uses change[2] to determine improve.
    
    if (len(f1_cf) != len(f2_cf)):
        er = 'Inputs must be the same length. '
        er+= str(len(f1_cf)) + ' != ' + str(len(f2_cf))
        raise ValueError(er)
    
    change = [f2_cf[k_cf] - f1_cf[k_cf] for k_cf in range(len(f1_cf))]
    
    if change[2] > 0:# More of the data was in the worst region
        improve = -1
    elif change[2] == 0:# No change
        improve = 0
    elif change[2] < 0: # Less of the data was in the worst region
        improve = 1
    else:
        er = 'Could not determine which is better.'
        er+= str(f2_cf[2]) + '-' + str(f1_cf[2]) + ' = ' + str(f2_cf[2] - f1_cf[2])
        raise RuntimeError(er)
    
    return improve, change
    

def run_motion_comfort_for_test(test_id):
    # Run motion_comfort on the 2 URIs for a test with test_id
    # and updates the tests dictionary with the results.
    input_plots = []
    titles = {'Ax':'Longitudinal Acceleration',
              'Ay':'Lateral Acceleration',
              'Az':'Vertical Acceleration',
              'Jx':'Longitudinal Jerk',
              'Jy':'Lateral Jerk',
              'Jz':'Vertical Jerk'}
    
    for i in range(2):# 0 = control, 1 = comparison
        mc = MotionComfort()
        mc.load_data(tests[test_id]['uri'][i], filter=4, to_map=True)
        mc.compute()
        
        temp_fractions = mc.fractions
        tests[test_id]['fractions'][i] = temp_fractions
        tests[test_id]['comfort'][i] = mc.comfort_values
        tests[test_id]['unix_time'][i] = mc.unix_time
        tests[test_id]['distance'][i] = mc.distance
        
        n_data = len(mc.comfort_values)
        
        tests[test_id]['length'][i] = n_data
        
        tests['total_fractions'][i][0] += temp_fractions[0]*n_data
        tests['total_fractions'][i][1] += temp_fractions[1]*n_data
        tests['total_fractions'][i][2] += temp_fractions[2]*n_data
        

        if i == 0: # If i==0, need to create the figures and set up the plots.
            
            for key in mc.present:
                temp_input_plot = mc.create_color_plot(mc.limits[key], mc.colors, 'default')
                temp_input_plot.title = Title(text=titles[key])
                temp_input_plot.line(mc.unix_time, mc.data[key], 
                             legend_label=labels[i], color=line_colors[i], line_dash=line_dash[i])
                temp_input_plot.xaxis.axis_label = 'unix time (s)'
                temp_input_plot.legend.location='top_right'#set up legends
                temp_input_plot.below[0].formatter.use_scientific = False

                if (key in ['Ax','Ay','Az']):
                    temp_input_plot.yaxis.axis_label = 'Acceleration (m/s^2)'
                elif (key in ['Jx','Jy','Jz']):
                    temp_input_plot.yaxis.axis_label = 'Jerk (m/s^3)'
                    
                input_plots.append([temp_input_plot])
            
            mc.make_map(support_path + '{:04d}'.format(test_id) + '_map_' + control_file_name + '.html')
            
        else: # If i == 1, need to add to the plots created when i was 0.
            mc.make_map(support_path + '{:04d}'.format(test_id) + '_map_' + comparison_file_name + '.html')
            for key in mc.present:
                plot_ind = mc.present.index(key)
                input_plots[plot_ind][0].line(mc.unix_time, mc.data[key], 
                             legend_label=labels[i], color=line_colors[i], line_dash=line_dash[i])
                
                input_plots[plot_ind][0].legend.click_policy='hide'
  
                if (plot_ind > 0):
                    input_plots[-1][0].x_range = input_plots[0][0].x_range #Link axes
        
    input_grid = gridplot(input_plots)
    output_file(support_path + '{:04d}'.format(test_id) + '_inputs.html', 
                title='{:04d}'.format(test_id) + '_inputs')
    save(column(input_grid))
    
    tests[test_id]['improve'], tests[test_id]['change'] = compare_fractions(tests[test_id]['fractions'][0],
                                                                            tests[test_id]['fractions'][1])
    del input_grid, input_plots
    
def plot_comforts(x_axis_data, x_axis_label, comfort_data):
    # Take in the information necessary to create an overlay of 2 comfort plots
    # and returns the figure containing the plot
    # INPUTS:
    #    x_axis_data = list of lists of data to put on the x-axis [line 1 data, line 2 data]
    #    x_axis_label = Text to appear on the label for the x-axis (usually unix_time or distance)
    #    comfort_data = list of lists of comfort data to put on the y-axis [line 1 data, line 2 data] 
    
    mc = MotionComfort()
    
    temp_limits = [[],[]]
    label_over = {0:'',0.5:mc.labels[0],len(mc.labels):''}
    for j in range(len(mc.labels)-1):
        temp_limits[0].insert(0, -1*(j+1))
        temp_limits[1].append(j+1)
        label_over[j+1.5] = mc.labels[j+1]
        label_over[j+1] = ''

    temp_comfort_plot = mc.create_color_plot(temp_limits, mc.colors, 'default') # Prepare plots
    temp_comfort_plot.title = Title(text='Comfort Level')
    temp_comfort_plot.yaxis.major_label_overrides = label_over
    temp_comfort_plot.below[0].formatter.use_scientific = False
    temp_comfort_plot.xaxis.axis_label = x_axis_label
    temp_comfort_plot.y_range.start = 0
    temp_comfort_plot.y_range.end = len(mc.labels)
    temp_comfort_plot.legend.location='top_right'
               
    for i in range(2):
        x_axis_data_sm, comfort_data_sm = mc.replace_constant_data(x_axis_data[i], comfort_data[i]) # Remove redundant data
        temp_comfort_plot.line(x_axis_data_sm, comfort_data_sm, legend_label=labels[i],
                               color=line_colors[i], line_dash=line_dash[i])
    
    temp_comfort_plot.legend.click_policy='hide'
    
    return temp_comfort_plot

def plot_fractions(fractions, title):
    # Make and return a bar chart for the fractions determined in mc.compute().

    rounded_frac = [round(k_pf,5) for k_pf in fractions]
    
    labels=['comfortable','not comfortable','unacceptable']
    colors=['green','yellow','red']

    source_pf = ColumnDataSource({'labels':labels,
                                  'y':fractions,
                                  'color':colors,
                                  'rounded':rounded_frac})

    out_plot = figure(plot_width=300, plot_height=200,
                     y_axis_label='fraction of data in range',
                     x_range=labels, title=title)
    out_plot.vbar(x='labels',bottom=0, top='y', color='color',
                     source=source_pf, width=0.7)
    lab_pf = LabelSet(x='labels',y='y', text='rounded',
                     source=source_pf, x_offset=-30)
    out_plot.add_layout(lab_pf)
    # Make sure there is space for the labels.
    out_plot.y_range.end = np.max(fractions) + 0.1
    
    return out_plot  


def test_output(test_id):
    # organize the output from a single test into a coherent row of output 
    if tests[test_id]['improve'] == 1:
        improve = 'better than'
    elif tests[test_id]['improve'] == -1:
        improve = 'worse than'
    else:
        improve = 'not different from'
    
    unacceptable_diff = tests[test_id]['change'][2]
    top_space = Div(text= "<a id='" + '{:04d}'.format(test_id) + "'>  </a>" )
    test_overview = Div(text=f"<h2>ID: {test_id} ,  {comparison} is {improve} {control}.  " +
                        f" (Change to unacceptable: {unacceptable_diff})</h2>" )
    test_name = Div(text='Name:  ' + tests[test_id]['name'])
    test_title = Div(text='title: ' + tests[test_id]['title'])
    
    argus_href_control = "<a href = 'https://argus.zooxlabs.com/uri?primaryUri=" + new_uri(tests[test_id]['uri'][0])
    argus_href_control+= "'>" + tests[test_id]['uri'][0] + " </a>"
    argus_href_comparison = "<a href = 'https://argus.zooxlabs.com/uri?primaryUri=" + new_uri(tests[test_id]['uri'][1])
    argus_href_comparison+= "'>" + tests[test_id]['uri'][1] + " </a>"
    
    argus_compare_href = "<a href = 'https://argus.zooxlabs.com/uri?primaryUri=" + new_uri(tests[test_id]['uri'][0])
    argus_compare_href+= "&comparisonUri=" + new_uri(tests[test_id]['uri'][1])
    argus_compare_href+= '&primaryNickname=' + control + '&comparisonNickname=' + comparison
    argus_compare_href+= "'>" + ' Comparison ' + " </a>"
    
    control_map_href = "<a href = '" + support_dir_name + '/' + '{:04d}'.format(test_id) + '_map_' + control_file_name + '.html'
    control_map_href+= "'>" + '{:04d}'.format(test_id) + '_map_' + control_file_name + '.html' + " </a>"
    comparison_map_href = "<a href = '" + support_dir_name + '/' + '{:04d}'.format(test_id) + '_map_' + comparison_file_name + '.html'
    comparison_map_href+= "'>" + '{:04d}'.format(test_id)  + '_map_' + comparison_file_name + '.html' + " </a>"
    
    input_plot_href = "<a href = '" + support_dir_name + '/' + '{:04d}'.format(test_id) + '_inputs.html'
    input_plot_href+= "'>" + '{:04d}'.format(test_id) + '_inputs.html' + " </a>"
    
    test_control_uri = Div(text = '    '+ control+ ' URI:  ' + argus_href_control)
    control_comfort_link = Div(text = '    ' + control + '  comfort map: ' + control_map_href)
    test_comparison_uri = Div(text = '     ' + comparison + '   URI: ' + argus_href_comparison)
    comparison_comfort_link = Div(text = '    ' + comparison + '  comfort map: ' + comparison_map_href)

    argus_compare_link = Div(text = '    Comparison in Argus: ' + argus_compare_href)
    
    input_plot_link = Div(text = '    Input plots: ' + input_plot_href)
    
    frac_plots = [plot_fractions(tests[test_id]['fractions'][0], control),
                  plot_fractions(tests[test_id]['fractions'][1], comparison),
                  plot_fractions(tests[test_id]['change'], 'Change')]
    
    comfort_tabs = []
    unit_string = [' (s)', ' (m)']
    for i,x_label in enumerate(['unix_time','distance']):
        comfort_tabs.append(Panel(child=plot_comforts(tests[test_id][x_label], x_label+unit_string[i], tests[test_id]['comfort']),
                                  title=x_label))

    
    comfort_tab = Tabs(tabs=comfort_tabs)
    
    test_plots = row(comfort_tab, *frac_plots)
    
    col = column(top_space, test_overview, test_name, test_title, test_control_uri,
                 control_comfort_link, test_comparison_uri, comparison_comfort_link,
                 input_plot_link, argus_compare_link, test_plots)
    
    return row(col)
    
    
def new_uri(uri):
    # Takes the given uri, URL encodes the whole thing
    return urllib.parse.quote(uri)

########################################################################
###   MAIN   MAIN   MAIN   MAIN   MAIN   MAIN   MAIN   MAIN   MAIN   ###
########################################################################
# Format of tests dictionary:
#   tests = { 'length': number of tests,
#             'ids': list of ids,
#             'dropped': list of ids for data that was ignored,
#             'total_improve': is comparison better than control overall? -1=worse, 0=no change, 1=better,
#             'total_fractions': running total fraction value across tests for [control, comparison]
#             'total_change': list of changes between total_fractions                                
#             id_number(int): {
#                              'name': name of test,
#                              'title': title of test,
#                              'result': [Control result, Comparison result],
#                              'uri': [Control URI, Comparison URI],
#                              'length': Number of data points for [Control, Comparison],
#                              'improve': is comparison better than control? -1=worse, 0=no change, 1=better,
#                              'change': list of changes to each fraction,
#                              'fractions': fraction data for [Control, Comparison],
#                              'comfort': comfort data for [Control, Comparison],
#                              'unix_time': unix time data for [Control, Comparison],
#                              'distance': distance data for [Control, Comparison],
#                             }
#           }
global tests, labels, line_colors, line_dash, control, comparison, control_file_name, comparison_file_name

#Custom settings  
######################
control = 'Master/original_config' # Name of the control branch to be visualized in the report
comparison = 'Master/changed_config' # Name of the comparicon branch to be visualized in the report
input_path = '/home/kvlasiuk/tryStuff/config_0524/config_comfort_chum.tsv'#'/home/kvlasiuk/tryStuff/slac_comfort/slac_empty_comfort.tsv' # Define tab seperated list of uris
output_path = '/home/kvlasiuk/tryStuff/config_0524/'#'/home/kvlasiuk/tryStuff/slac_comfort/' # Where to save the output files
output_file_name = 'config_0524.html' # Name of output .html file
support_dir_name = 'config_0524_maps' # Name of subdirectory (in output_path) where map files will be save.
     
                    
labels = [control,comparison] # Labels for [control, comparison] lines on plots
line_colors = ['blue','magenta'] # Colors for [control, comparison] lines on plots
line_dash = ['solid','dashed'] # Line styles for [control, comparison] lines on plots
######################
                    
control_file_name = re.sub(r"[-()\"#/@;:<>{}`+=~|.!?,]", '_', control).lower()
comparison_file_name =  re.sub(r"[-()\"#/@;:<>{}`+=~|.!?,]", '_', comparison).lower()

start_time = time.time()

print(f'Start_time =  {start_time}')
                    
support_path = output_path + support_dir_name + '/'
if os.path.exists(support_path):
    shutil.rmtree(support_path)

os.makedirs(support_path)

tests = read_test_list(input_path) # Read it in

# For each test, run motion_comfort(), collect and organize output
improve_count = [0,0,0] # Running count of how many [improved, didn't change, got worse]
test_output_rows = []
test_output_rows_better = []
test_output_rows_worse = []
test_diff = []              
total_n_data = [0,0]
for test_id in tests['ids']:
    print('Processing id: ',test_id)
    run_motion_comfort_for_test(test_id)
    test_output_rows.append(test_output(test_id))
    if tests[test_id]['improve'] == 1:
        improve_count[0] += 1
        test_output_rows_better.append(test_output(test_id))
    elif tests[test_id]['improve'] == 0:
        improve_count[1] += 1
    else:
        improve_count[2] += 1
        test_output_rows_worse.append(test_output(test_id))
        
    print(f'    Improved: {improve_count[0]}, no change: {improve_count[1]}, worse: {improve_count[2]}')
        
    total_n_data[0] += tests[test_id]['length'][0]
    total_n_data[1] += tests[test_id]['length'][1]
    test_diff.append(np.abs(tests[test_id]['fractions'][1][2] - tests[test_id]['fractions'][0][2]))
    

for i in range(2): # Make the total fraction an average
    tests['total_fractions'][i] = [tests['total_fractions'][i][k]/total_n_data[i] for k in range(3)] 
                                      
tests['total_improve'], tests['total_change'] = compare_fractions(tests['total_fractions'][0],
                                                                  tests['total_fractions'][1])
ids_to_sort = copy.deepcopy(tests['ids'])
ids_sorted_by_diff = [k2 for k1,k2 in sorted(zip(test_diff,ids_to_sort), reverse=True)]
diff_link_text = "<a href = " + output_file_name + "#" + '{:04d}'.format(ids_sorted_by_diff[0]) + "> "
diff_link_text+= '{:04d}'.format(ids_sorted_by_diff[0]) + "</a>"
for id_ in ids_sorted_by_diff[1:]:
    diff_link_text += ", <a href = " + output_file_name + "#" + '{:04d}'.format(id_) + ">"
    diff_link_text += '{:04d}'.format(id_) + "</a>"

most_diff_tests = row(Div(text='Sorted by biggest differences: ' + diff_link_text, width = 600))

# Display the results
if tests['total_improve'] == 1:
    improve = 'better than'
elif tests['total_improve'] == -1:
    improve = 'worse than'
else:
    improve = 'not different from'
    

improve_par = Div(text = f'<h2> Overview: {comparison} is {improve} {control}. </h2>', width = 600)
ratio0_par = Div(text = f"<h3>      {improve_count[0]} of {str(tests['length'])} tests showed improvement. </h3>")
better_link = Div(text = "<h3><a href = '" + support_dir_name + "/" + output_file_name.split('.')[0] + "_better.html'>" +
                       "Showed improvement. </a></h3>")
ratio1_par = Div(text = f"<h3>      {improve_count[1]} of {str(tests['length'])} tests showed no change. </h3>")
ratio2_par = Div(text = f"<h3>      {improve_count[2]} of {str(tests['length'])} tests got worse. </h3>")
worse_link = Div(text = "<h3><a href = '" + support_dir_name + "/" + output_file_name.split('.')[0] + "_worse.html'>" +
                 "Got worse. </a></h3>")
if len(tests['dropped']) == 1:
    was_were = 'was'
    plurals = ''
else:
    was_were = 'were'
    plurals = 's'
ignore_par = Div(text = f"<a>      {len(tests['dropped'])} test{plurals} in original set {was_were} ignored. </a>")


overview_plots = row(plot_fractions(tests['total_fractions'][0], control ),
                     plot_fractions(tests['total_fractions'][1], comparison ),
                     plot_fractions(tests['total_change'], 'Change'))
overview = column(row(improve_par), row(ratio0_par, better_link),row(ratio1_par), row(ratio2_par, worse_link),
                  row(ignore_par), overview_plots, most_diff_tests)


output_file(output_path + output_file_name, title='run_uri_tests')

save(column(row(overview),*test_output_rows))

ratio_par_better = Div(text = f"<h3>      {improve_count[0]} of {str(tests['length'])} tests showed improvement. </h3>")
output_file(output_path + support_dir_name + '/' + output_file_name.split('.')[0]+'_better.html',
            title='run_uri_tests Better')
save(column(row(ratio_par_better),*test_output_rows_better))

ratio_par_worse = Div(text = f"<h3>      {improve_count[2]} of {str(tests['length'])} tests got worse. </h3>")
output_file(output_path + support_dir_name + '/' + output_file_name.split('.')[0]+'_worse.html', title='run_uri_tests Worse')
save(column(row(ratio_par_worse),*test_output_rows_worse))

run_time = time.time() - start_time
print(f'Output saved to {output_path + output_file_name}')
print(f'This run took {run_time} seconds.')

In [ ]:
print(f'This run took  seconds.')